In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'GrossProfit', '營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
year: 107
season: 1
營業毛利（毛損）
year: 106
season: 4
營業毛利（毛損）
year: 106
season: 3
營業毛利（毛損）
year: 106
season: 2
營業毛利（毛損）
year: 106
season: 1
營業毛利（毛損）
year: 105
season: 4
營業毛利（毛損）
year: 105
season: 3
營業毛利（毛損）
year: 105
season: 2
營業毛利（毛損）
year: 105
season: 1
營業毛利（毛損）
year: 104
season: 4
營業毛利（毛損）
year: 104
season: 3
營業毛利（毛損）
year: 104
season: 2


公司代號     公司名稱 GrossProfit_107Q2 GrossProfit_107Q1 GrossProfit_106Q4  \
0    2809     京城銀行               NaN               NaN               NaN   
1    1101       台泥          16059356           5790640          18912914   
2    1102       亞泥           9329556           3329473          10171018   
3    1103       嘉泥            144835             54830            282321   
4    1104     環球水泥            265250            138524            537908   
5    1108     幸福水泥             62377             20566            128501   
6    1109     信大水泥            822279            241008           1256014   
7    1110       東泥             67981             34457            -43205   
8    1201     味全公司           2665169           1104857           5553412   
9    1203     味王公司            965054            488478           2020256   
10   1210     大成長城           4984732           2552191          10232733   
11   1213       大飲             30359             16020             68492   
12   1215     卜蜂企業           1349590            732606           3327986   
13   1216       統一          73191320          35429055         132740671   
14   1217      愛之味            654411            325598           1304671   
15   1218     泰山企業            684682            305219           1331364   
16   1219     福壽實業            506714            268613            896460   
17   1220       台榮            165436             65957            274884   
18   1225      福懋油            481178            251047           1035870   
19   1227       佳格           3679845           2289204           7399955   
20   1229     聯華實業            409394            203445           1025092   
21   1231     聯華食品            771794            459088           1445489   
22   1232      大統益            889406            429340           1685216   
23   1233       天仁            629296            321597           1212380   
24   1234       黑松           1079837            474380           2335035   
25   1235       興泰               -73              -621              4798   
26   1236     宏亞食品            219353            161160            502744   
27   1256  鮮活果汁-KY            553694            221370            872790   
28   1262    綠悅-KY             48037             98650           1394442   
29   1301       台塑          20868575           9349215          33469176   
30   1303     南亞塑膠          27436919          13756954          49934342   
31   1304       台聚           3714047           1845606           7126932   
32   1305       華夏           1769782            970114           2776931   
33   1307     三芳化工            963262            553730           2903725   
34   1308       亞聚            141446             77798            697076   
35   1309     台達化工            842975            375252           1433704   
36   1310       台苯           1168179            546139           1689216   
37   1312     國喬石化           2178914           1124826           3793985   
38   1313       聯成           2039588           1019444           3860351   
39   1314      中石化           2644808           1257893           5371019   
40   1315     達新工業            164247             82189            443657   
41   1316       上曜            397366            249091            633976   
42   1319       東陽           2720890           1463316           5925374   
43   1321       大洋             91978             80406            251921   
44   1323       永裕            437095            195229            766312   
45   1324     地球工業             93690             39128            186809   
46   1325       恒大             51666             26465            118147   
47   1326       台化          29936538          15750882          53196202   
48   1337    再生-KY            -84760            -42543            691365   
49   1338    廣華-KY            987748            501805           2104327   
50   1339       昭輝            388939            216958            878555   
51   1340    勝悅-KY            283193            14031

In [ ]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_eps_sii.columns # the column index
#idx = df_eps_sii.index # the row index
numOfRows_s = df_gross_profit_sii.shape[0] #len(df_gross_profit_sii) #len(df_gross_profit_sii.index)
numOfColumns_s = df_gross_profit_sii.shape[1] #len(df_gross_profit_sii.columns)
headNameOfColumns_s = df_gross_profit_sii.columns

print(numOfColumns_s)
df_gross_profit_sii

for row_index_s in range(0, numOfRows_s):
    for col_index_s in range(0, numOfColumns_s):
        #print(df_gross_profit_sii.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_gross_profit_sii.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_gross_profit_sii.columns.values[col_index_s]): # if (df_eps_sii.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_gross_profit_sii.columns.values[col_index_s]):
                continue
            elif (u"公司名稱" in df_gross_profit_sii.columns.values[col_index_s]):
                continue
            elif (col_index_s == numOfColumns_s-1):
                continue
            else:
                df_gross_profit_sii.iloc[row_index_s, col_index_s] = float(df_gross_profit_sii.iloc[row_index_s, col_index_s]) - float(df_gross_profit_sii.iloc[row_index_s, col_index_s+1])

df_gross_profit_sii              

In [5]:
df_gross_profit_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'GrossProfit', '營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
year: 107
season: 1
營業毛利（毛損）
year: 106
season: 4
營業毛利（毛損）
year: 106
season: 3
營業毛利（毛損）
year: 106
season: 2
營業毛利（毛損）
year: 106
season: 1
營業毛利（毛損）
year: 105
season: 4
營業毛利（毛損）
year: 105
season: 3
營業毛利（毛損）
year: 105
season: 2
營業毛利（毛損）
year: 105
season: 1
營業毛利（毛損）
year: 104
season: 4
營業毛利（毛損）
year: 104
season: 3
營業毛利（毛損）
year: 104
season: 2


公司代號    公司名稱 GrossProfit_107Q2 GrossProfit_107Q1 GrossProfit_106Q4  \
0    6026    福邦證券               NaN               NaN               NaN   
1    1258   其祥-KY            207804            111964            438375   
2    1259      安心            633224            300863           1276789   
3    1264      德麥            713224            356578           1385575   
4    1333     恩得利             21799             10606             50907   
5    1336      台翰            184320             90384            386849   
6    1565    精華光學           1214155            580094           2544591   
7    1566      捷邦            339492            158604            762675   
8    1569      濱川            292221            141677            810337   
9    1570    力肯實業             73344             30939            189520   
10   1580    新麥企業            795853            345430           1897745   
11   1584    精剛精密             -2720              5585             28645   
12   1586    和勤精機            221326             99280            456121   
13   1591   駿吉-KY             45006             11650             70370   
14   1593      祺驊             90259             40796            261398   
15   1595    川寶科技            258221            118570            432536   
16   1597      直得            526619            241486            622967   
17   1599     宏佳騰            197239             62450            592466   
18   1742      台蠟            -31648              4553             44916   
19   1752      南光            273087            132171            516345   
20   1777      生泰            127995             63015            199828   
21   1781    合世生醫             21102              4721             53074   
22   1784    訊聯生技            215263            109602            366203   
23   1785     光洋科           1053104            475117           1649445   
24   1787     福盈科            317451            150144            595719   
25   1788    杏昌生技            349793            168364            668577   
26   1795    美時製藥           1466165            683280           3079674   
27   1799      易威             17321              9097             36446   
28   1813     寶利徠             34530             15826             82193   
29   1815    富喬工業            662257            322084           1309981   
30   2035    唐榮公司            -67749            -73079            540270   
31   2061      風青             37167             15368             75209   
32   2063      世鎧            161401             77992            278448   
33   2064      晉椿            112212             64842            227669   
34   2066      世德            163496             73205            383881   
35   2067      嘉鋼            125266             54169            194613   
36   2221    大甲永和            141236             65253            230026   
37   2230      泰茂             40974             16171            103826   
38   2233      宇隆            530572            268628            957212   
39   2235      謚源             81330             44231            237777   
40   2596    綠意開發            484096            264675            485117   
41   2640     大車隊            424731            217382            786943   
42   2641    正德海運             85914             39129             96100   
43   2643      捷迅            124552             59941            280907   
44   2718      晶悅              1299              4698             19167   
45   2719     燦星旅            150516             57678            318666   
46   2724   富驛-KY              1539            -11261            112005   
47   2726   雅茗-KY            559235            278174           1088792   
48   2729    瓦城泰統           1149496            574821           2189895   
49   2732    六角國際            829818            390897           1370065   
50   2734     易飛網             84701             44033            155224   
51   2736      高野            145230             81214            341249   
52   2740      天蔥             

In [ ]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_gross_profit_otc.columns # the column index
#idx = df_gross_profit_otc.index # the row index
numOfRows_o = df_gross_profit_otc.shape[0] #len(df_gross_profit_otc) #len(df_gross_profit_otc.index)
numOfColumns_o = df_gross_profit_otc.shape[1] #len(df_gross_profit_otc.columns)
headNameOfColumns_o = df_gross_profit_otc.columns

print(numOfColumns_o)
df_gross_profit_otc

for row_index_o in range(0, numOfRows_o):
    for col_index_o in range(0, numOfColumns_o):
        #print(df_gross_profit_otc.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_gross_profit_otc.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_gross_profit_otc.columns.values[col_index_o]): # if (df_gross_profit_otc.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_gross_profit_otc.columns.values[col_index_o]):
                continue
            elif (u"公司名稱" in df_gross_profit_otc.columns.values[col_index_o]):
                continue
            elif (col_index_o == numOfColumns_o-1):
                continue
            else:
                df_gross_profit_otc.iloc[row_index_o, col_index_o] = float(df_gross_profit_otc.iloc[row_index_o, col_index_o]) - float(df_gross_profit_otc.iloc[row_index_o, col_index_o+1])

df_gross_profit_otc              

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號     公司名稱 GrossProfit_107Q2 GrossProfit_107Q1 GrossProfit_106Q4  \
0     2809     京城銀行               NaN               NaN               NaN   
1     1101       台泥          16059356           5790640          18912914   
2     1102       亞泥           9329556           3329473          10171018   
3     1103       嘉泥            144835             54830            282321   
4     1104     環球水泥            265250            138524            537908   
5     1108     幸福水泥             62377             20566            128501   
6     1109     信大水泥            822279            241008           1256014   
7     1110       東泥             67981             34457            -43205   
8     1201     味全公司           2665169           1104857           5553412   
9     1203     味王公司            965054            488478           2020256   
10    1210     大成長城           4984732           2552191          10232733   
11    1213       大飲             30359             16020             68492   
12    1215     卜蜂企業           1349590            732606           3327986   
13    1216       統一          73191320          35429055         132740671   
14    1217      愛之味            654411            325598           1304671   
15    1218     泰山企業            684682            305219           1331364   
16    1219     福壽實業            506714            268613            896460   
17    1220       台榮            165436             65957            274884   
18    1225      福懋油            481178            251047           1035870   
19    1227       佳格           3679845           2289204           7399955   
20    1229     聯華實業            409394            203445           1025092   
21    1231     聯華食品            771794            459088           1445489   
22    1232      大統益            889406            429340           1685216   
23    1233       天仁            629296            321597           1212380   
24    1234       黑松           1079837            474380           2335035   
25    1235       興泰               -73              -621              4798   
26    1236     宏亞食品            219353            161160            502744   
27    1256  鮮活果汁-KY            553694            221370            872790   
28    1262    綠悅-KY             48037             98650           1394442   
29    1301       台塑          20868575           9349215          33469176   
30    1303     南亞塑膠          27436919          13756954          49934342   
31    1304       台聚           3714047           1845606           7126932   
32    1305       華夏           1769782            970114           2776931   
33    1307     三芳化工            963262            553730           2903725   
34    1308       亞聚            141446             77798            697076   
35    1309     台達化工            842975            375252           1433704   
36    1310       台苯           1168179            546139           1689216   
37    1312     國喬石化           2178914           1124826           3793985   
38    1313       聯成           2039588           1019444           3860351   
39    1314      中石化           2644808           1257893           5371019   
40    1315     達新工業            164247             82189            443657   
41    1316       上曜            397366            249091            633976   
42    1319       東陽           2720890           1463316           5925374   
43    1321       大洋             91978             80406            251921   
44    1323       永裕            437095            195229            766312   
45    1324     地球工業             93690             39128            186809   
46    1325       恒大             51666             26465            118147   
47    1326       台化          29936538          15750882          53196202   
48    1337    再生-KY            -84760            -42543            691365   
49    1338    廣華-KY            987748            501805           2104327   
50    1339       昭輝            388939            216958            878555   
51

In [7]:
#檢查column資料型態

#df_eps.info() #non-null object
#df_eps.dtypes #object
#df_eps.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
GrossProfit_104Q4    float64
GrossProfit_104Q3    float64
GrossProfit_104Q2    float64
GrossProfit_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                   int64
公司名稱                  object
GrossProfit_107Q2    float64
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
GrossProfit_104Q4    float64
GrossProfit_104Q3    float64
GrossProfit_104Q2    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfit_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfit_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)])):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on=u'公司代號', how='inner')

df_gross_profit

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  GrossProfit_107Q2  GrossProfit_107Q1  GrossProfit_106Q4  \
0     2809     京城銀行                NaN                NaN                NaN   
1     1101       台泥         16059356.0          5790640.0         18912914.0   
2     1102       亞泥          9329556.0          3329473.0         10171018.0   
3     1103       嘉泥           144835.0            54830.0           282321.0   
4     1104     環球水泥           265250.0           138524.0           537908.0   
5     1108     幸福水泥            62377.0            20566.0           128501.0   
6     1109     信大水泥           822279.0           241008.0          1256014.0   
7     1110       東泥            67981.0            34457.0           -43205.0   
8     1201     味全公司          2665169.0          1104857.0          5553412.0   
9     1203     味王公司           965054.0           488478.0          2020256.0   
10    1210     大成長城          4984732.0          2552191.0         10232733.0   
11    1213       大飲            30359.0            16020.0            68492.0   
12    1215     卜蜂企業          1349590.0           732606.0          3327986.0   
13    1216       統一         73191320.0         35429055.0        132740671.0   
14    1217      愛之味           654411.0           325598.0          1304671.0   
15    1218     泰山企業           684682.0           305219.0          1331364.0   
16    1219     福壽實業           506714.0           268613.0           896460.0   
17    1220       台榮           165436.0            65957.0           274884.0   
18    1225      福懋油           481178.0           251047.0          1035870.0   
19    1227       佳格          3679845.0          2289204.0          7399955.0   
20    1229     聯華實業           409394.0           203445.0          1025092.0   
21    1231     聯華食品           771794.0           459088.0          1445489.0   
22    1232      大統益           889406.0           429340.0          1685216.0   
23    1233       天仁           629296.0           321597.0          1212380.0   
24    1234       黑松          1079837.0           474380.0          2335035.0   
25    1235       興泰              -73.0             -621.0             4798.0   
26    1236     宏亞食品           219353.0           161160.0           502744.0   
27    1256  鮮活果汁-KY           553694.0           221370.0           872790.0   
28    1262    綠悅-KY            48037.0            98650.0          1394442.0   
29    1301       台塑         20868575.0          9349215.0         33469176.0   
30    1303     南亞塑膠         27436919.0         13756954.0         49934342.0   
31    1304       台聚          3714047.0          1845606.0          7126932.0   
32    1305       華夏          1769782.0           970114.0          2776931.0   
33    1307     三芳化工           963262.0           553730.0          2903725.0   
34    1308       亞聚           141446.0            77798.0           697076.0   
35    1309     台達化工           842975.0           375252.0          1433704.0   
36    1310       台苯          1168179.0           546139.0          1689216.0   
37    1312     國喬石化          2178914.0          1124826.0          3793985.0   
38    1313       聯成          2039588.0          1019444.0          3860351.0   
39    1314      中石化          2644808.0          1257893.0          5371019.0   
40    1315     達新工業           164247.0            82189.0           443657.0   
41    1316       上曜           397366.0           249091.0           633976.0   
42    1319       東陽          2720890.0          1463316.0          5925374.0   
43    1321       大洋            91978.0            80406.0           251921.0   
44    1323       永裕           437095.0           195229.0           766312.0   
45    1324     地球工業            93690.0            39128.0           186809.0   
46    1325       恒大            51666.0            26465.0           118147.0   
47    1326       台化         29936538.0         15750882.0         53196202.0   
48    1337    再生-KY           -84760.0           -42543.0           691365.0   
49    

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_GrossProfit.xlsx', 'GrossProfit_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
